# ACESSORIES
### Võ Hửu Nghĩa - 2013304

#### IMPORT CÁC THƯ VIỆN CẦN THIẾT

In [36]:
import pyodbc
import pandas as pd
import numpy as np
import re
import random
from mlxtend.frequent_patterns import apriori, fpgrowth, association_rules
from mlxtend.preprocessing import TransactionEncoder

#### KẾT NỐI VỚI CƠ SỞ DỮ LIỆU SQL SERVER

In [37]:
server = 'VoHuuNghia'  # Change this to your SQL Server hostname
database = 'libol'  # Change this to your database name
driver = '{ODBC Driver 17 for SQL Server}' 

#### LẤY DỮ LIỆU TỪ BẢNG "An_pham_cho_muon" CHO VÀO DATAFRAME

In [38]:
connection_string = f"DRIVER={driver};SERVER={server};DATABASE={database};Trusted_Connection=yes;"
try:
    conn = pyodbc.connect(connection_string)
    cursor = conn.cursor()

    cursor.execute("SELECT @@version;")
    row = cursor.fetchone()
    print("Connected to SQL Server. Server version:", row[0])
    getHistoryQuery = "select * from An_pham_cho_muon"
    df_History = pd.read_sql(getHistoryQuery, conn)
except pyodbc.Error as e:
    print(f"Error connecting to SQL Server: {e}")

Connected to SQL Server. Server version: Microsoft SQL Server 2022 (RTM) - 16.0.1000.6 (X64) 
	Oct  8 2022 05:58:25 
	Copyright (C) 2022 Microsoft Corporation
	Express Edition (64-bit) on Windows 10 Pro 10.0 <X64> (Build 22631: ) (Hypervisor)



C:\Users\vhngh\AppData\Local\Temp\ipykernel_10524\1745608300.py:10: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  df_History = pd.read_sql(getHistoryQuery, conn)


In [39]:
df_History.head()

Tai_lieu_ID Ma_xep_gia           Ngay_muon            Ngay_tra  So_the_ID  \
0          665  skv003743 2002-10-22 23:31:00 2003-06-06 11:20:11       3060   
1          701  skv003812 2002-10-22 23:32:00 2003-06-06 11:20:44       3060   
2          820  skv003913 2002-10-22 23:37:00 2003-06-06 11:25:40       3060   
3          876  SKV005496 2002-11-10 20:22:00 2003-06-25 09:09:50       3364   
4          892  SKV006782 2002-11-11 13:47:00 2003-04-01 13:41:54       2825   

   So_luot_gia_han  LoanType  Note    ID  CirID  
0                0         1  None  3288     13  
1                0         1  None  3290     13  
2                0         1  None  3295     13  
3                0         1  None  7578     13  
4                0         1  None  7787     13

In [40]:
df_History['Ngay_muon'] = pd.to_datetime(df_History['Ngay_muon']).dt.date

In [41]:
df_History.head()

Tai_lieu_ID Ma_xep_gia   Ngay_muon            Ngay_tra  So_the_ID  \
0          665  skv003743  2002-10-22 2003-06-06 11:20:11       3060   
1          701  skv003812  2002-10-22 2003-06-06 11:20:44       3060   
2          820  skv003913  2002-10-22 2003-06-06 11:25:40       3060   
3          876  SKV005496  2002-11-10 2003-06-25 09:09:50       3364   
4          892  SKV006782  2002-11-11 2003-04-01 13:41:54       2825   

   So_luot_gia_han  LoanType  Note    ID  CirID  
0                0         1  None  3288     13  
1                0         1  None  3290     13  
2                0         1  None  3295     13  
3                0         1  None  7578     13  
4                0         1  None  7787     13

#### Tạo danh sách 'Tai_lieu_ID' mượn trong cùng ngày

In [42]:
transactions = df_History.groupby('Ngay_muon')['Tai_lieu_ID'].apply(list).values.tolist()

#### HIỂN THỊ 10 GIAO DỊCH ĐẦU TIÊN

In [43]:
print(transactions[:10])

[[665, 701, 820], [876], [892], [1724], [1886, 519], [3307], [734], [326], [738, 832, 751, 848, 749, 876], [4065, 5810, 5862, 5863]]


#### Chuẩn bị dữ liệu giao dịch cho phân tích khai phá luật kết hợp

In [44]:
te = TransactionEncoder()
te_ary = te.fit(transactions).transform(transactions) #xác định các mục (items) duy nhất trong dữ liệu giao dịch.
df_trans = pd.DataFrame(te_ary, columns=te.columns_) # chuyển đổi tập dữ liệu transactions thành một ma trận boolean

#### Tìm tập phổ biến bằng thuật toán Apriori

In [45]:
frequent_itemsets = apriori(df_trans, min_support=0.01, use_colnames=True)

#### Hiển thị kết quả

In [46]:
print("Frequent Itemsets using Apriori:\n", frequent_itemsets)

Frequent Itemsets using Apriori:
        support                                           itemsets
0     0.021268                                            (11070)
1     0.024949                                            (11071)
2     0.013497                                            (11072)
3     0.067485                                            (11073)
4     0.026585                                            (11076)
...        ...                                                ...
1453  0.010225         (57771, 57774, 36917, 36792, 37017, 37018)
1454  0.010225         (52006, 38736, 37137, 36917, 36792, 37017)
1455  0.010225         (57771, 57774, 36792, 36920, 37017, 37018)
1456  0.010225         (57771, 57774, 36917, 36920, 37017, 37018)
1457  0.010225  (57771, 57774, 36917, 36792, 36920, 37017, 37018)

[1458 rows x 2 columns]


####  Tìm ra các luật kết hợp từ tập phổ biến trên

In [47]:
rules = association_rules(frequent_itemsets, metric="lift", min_threshold=0.05) # lift đo độ liên kết giữa 2 items, min_threshold giới hạn min của lift
print("Association Rules using Apriori:\n",rules)

Association Rules using Apriori:
      antecedents                                 consequents  \
0        (11070)                                     (11071)   
1        (11071)                                     (11070)   
2        (11128)                                     (11070)   
3        (11070)                                     (11128)   
4        (11140)                                     (11070)   
...          ...                                         ...   
9029     (36917)  (37018, 57771, 57774, 36792, 37017, 36920)   
9030     (36792)  (57771, 57774, 36917, 36920, 37017, 37018)   
9031     (36920)  (57771, 57774, 36917, 36792, 37017, 37018)   
9032     (37017)  (37018, 57771, 57774, 36917, 36792, 36920)   
9033     (37018)  (57771, 57774, 36917, 36792, 37017, 36920)   

      antecedent support  consequent support   support  confidence       lift  \
0               0.021268            0.024949  0.011043    0.519231  20.811791   
1               0.024949           

#### Tìm tập phổ biến bằng thuật toán FP-Growth

In [48]:
frequent_itemsets_fp = fpgrowth(df_trans, min_support=0.01, use_colnames=True)

#### Hiển thị kết quả

In [49]:
print("Frequent Itemsets using FP-Growth:\n",frequent_itemsets_fp)

Frequent Itemsets using FP-Growth:
        support                                           itemsets
0     0.032311                                            (11128)
1     0.029039                                            (11140)
2     0.024949                                            (11071)
3     0.021268                                            (11070)
4     0.013497                                            (11072)
...        ...                                                ...
1453  0.010225  (57771, 57774, 36917, 36792, 36920, 37017, 37018)
1454  0.010634                                     (59641, 37018)
1455  0.010225                                     (59641, 36917)
1456  0.010225                                     (36792, 59641)
1457  0.010225                              (36792, 59641, 37018)

[1458 rows x 2 columns]


####  Tìm ra các luật kết hợp từ tập phổ biến trên

In [50]:
rules_fp = association_rules(frequent_itemsets_fp, metric="confidence", min_threshold=0.05)
print("Association Rules using FP-Growth:\n",rules_fp)

Association Rules using FP-Growth:
          antecedents     consequents  antecedent support  consequent support  \
0            (11128)         (14658)            0.032311            0.037628   
1            (14658)         (11128)            0.037628            0.032311   
2            (11128)         (11073)            0.032311            0.067485   
3            (11073)         (11128)            0.067485            0.032311   
4            (11128)         (12495)            0.032311            0.057260   
...              ...             ...                 ...                 ...   
9029  (36792, 37018)         (59641)            0.035583            0.013088   
9030  (59641, 37018)         (36792)            0.010634            0.086299   
9031         (36792)  (59641, 37018)            0.086299            0.010634   
9032         (59641)  (36792, 37018)            0.013088            0.035583   
9033         (37018)  (36792, 59641)            0.053579            0.010225   

   

#### Hiển thị kết quả trực quan kết quả của thuật toán apriori

In [51]:
# Tạo một hàm print_association_rule để in ra rule
def print_association_rule(rule):
    antecedents = ', '.join(map(str, rule['antecedents']))
    consequents = ', '.join(map(str, rule['consequents']))
    print(f"Rule: {antecedents} -> {consequents}")
    print(f"- Support: {rule['support']:.3f}")
    print(f"- Confidence: {rule['confidence']:.3f}")
    print(f"- Lift: {rule['lift']:.3f}")
    print("-" * 50)

# Lặp qua từng rule và in ra bằng hàm print_association_rule
for _, rule in rules_fp.iterrows():
    print_association_rule(rule)

Rule: 11128 -> 14658
- Support: 0.011
- Confidence: 0.329
- Lift: 8.747
--------------------------------------------------
Rule: 14658 -> 11128
- Support: 0.011
- Confidence: 0.283
- Lift: 8.747
--------------------------------------------------
Rule: 11128 -> 11073
- Support: 0.012
- Confidence: 0.367
- Lift: 5.440
--------------------------------------------------
Rule: 11073 -> 11128
- Support: 0.012
- Confidence: 0.176
- Lift: 5.440
--------------------------------------------------
Rule: 11128 -> 12495
- Support: 0.010
- Confidence: 0.316
- Lift: 5.527
--------------------------------------------------
Rule: 12495 -> 11128
- Support: 0.010
- Confidence: 0.179
- Lift: 5.527
--------------------------------------------------
Rule: 11128 -> 11140
- Support: 0.016
- Confidence: 0.481
- Lift: 16.564
--------------------------------------------------
Rule: 11140 -> 11128
- Support: 0.016
- Confidence: 0.535
- Lift: 16.564
--------------------------------------------------
Rule: 12496 ->

#### Đề xuất các cuốn sách dựa trên association rules

In [52]:
# def suggest_books(book_id, rules, num_suggestions=5):
#     suggestions = []
#     for index, rule in rules.iterrows():
#         if book_id in rule['antecedents']:
#             consequents = list(rule['consequents'])
#             for consequent in consequents:
#                 if consequent not in suggestions:
#                     suggestions.append(consequent)  
#                 if len(suggestions) >= num_suggestions:
#                     break
#         if len(suggestions) >= num_suggestions:
#             break
#     return suggestions

#### Kết nối với csdl sql server

In [53]:
server = 'VoHuuNghia'  # Change this to your SQL Server hostname
database = 'library_warehouse'  # Change this to your database name
driver = '{ODBC Driver 17 for SQL Server}' 

#### Lấy tất cả dữ liệu từ bảng DimBook

In [54]:
connection_string = f"DRIVER={driver};SERVER={server};DATABASE={database};Trusted_Connection=yes;"
try:
    conn = pyodbc.connect(connection_string)
    cursor = conn.cursor()

    cursor.execute("SELECT @@version;")
    row = cursor.fetchone()
    print("Connected to SQL Server. Server version:", row[0])
    getBook = "select * from DimBook"
    df_Book = pd.read_sql(getBook, conn)
except pyodbc.Error as e:
    print(f"Error connecting to SQL Server: {e}")

Connected to SQL Server. Server version: Microsoft SQL Server 2022 (RTM) - 16.0.1000.6 (X64) 
	Oct  8 2022 05:58:25 
	Copyright (C) 2022 Microsoft Corporation
	Express Edition (64-bit) on Windows 10 Pro 10.0 <X64> (Build 22631: ) (Hypervisor)



C:\Users\vhngh\AppData\Local\Temp\ipykernel_10524\2199320381.py:10: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  df_Book = pd.read_sql(getBook, conn)


#### Hiển thị mẫu của DimBook

In [55]:
df_Book.sample(5)

Tailieu_ID  Tacgia_ID  \
7421        10986     5529.0   
11637       15191     6125.0   
31725       26025     9606.0   
8828        12349    11404.0   
1520         3392     2575.0   

                                            Tailieu_Name    MaTailieu  
7421   $aCẩm nang giúp bạn thành công trong các kỳ th...  SK040010991  
11637  $aThiết kế máy công cụ :$bTập 1 /$cNguyễn Anh ...  SK050015196  
31725  $aTìm hiểu hệ điều hành Linux và một số phần m...  SK080026034  
8828   $aNghiên cứu áp dụng công nghệ sinh học kỵ khí...  SK050012351  
1520                             $aHướng dẫn chơi cờ vây  SK020003411

#### Xử lí dữ liệu cột tailieu_name

In [56]:
import re

In [57]:
def clean_name(tailieu_name):
    match = re.search(r'\$a([^$]*)', tailieu_name)
    if match:
        clean_name = match.group(1).strip()
        clean_name = re.sub(r'[/:]', '', clean_name).lower()
        return clean_name
    return tailieu_name


#### Ghi đè kết quả ngược vào chính cột Tailieu_Name

In [58]:
df_Book['Tailieu_Name'] = df_Book['Tailieu_Name'].apply(clean_name)

#### Hiển thị kết quả sau khi đã xử lí

In [59]:
df_Book.sample(5)

Tailieu_ID  Tacgia_ID  \
24995       27651     1281.0   
9827        13504    12540.0   
34885       38151    29208.0   
14507       17200     7660.0   
26476       29235    20290.0   

                                            Tailieu_Name    MaTailieu  
24995           plc lập trình ứng dụng trong công nghiệp  SK090027652  
9827            approved practices in pasture management  SK050013509  
34885  hoàn thiện công tác đào tạo nguồn nhân lực tại...  SK130038158  
14507  chinh phục coreldraw x3 một cách nhanh chóng v...  SK060017201  
26476              tự pha chế thức uống bổ dưỡng - tập 1  SK100029235

#### Xử lí và lưu các từ vào trong copus

In [60]:
data = []

for index, rule in rules_fp.iterrows():
    antecedents_books = ', '.join(df_Book[df_Book['Tailieu_ID'].isin(rule['antecedents'])]['Tailieu_Name'])
    consequents_books = ', '.join(df_Book[df_Book['Tailieu_ID'].isin(rule['consequents'])]['Tailieu_Name'])
    print(f"Rule: {antecedents_books} -> {consequents_books}")
    print(f"Support: {rule['support']}")
    print(f"Confidence: {rule['confidence']}")
    print(f"Lift: {rule['lift']}")
    print("=====================================")
    rule_info = {
        "Rule": f"{antecedents_books} -> {consequents_books}",
        "Support": rule['support'],
        "Confidence": rule['confidence'],
        "Lift": rule['lift']
    }
    data.append(rule_info)


Rule: bài tập toán học cao cấp -> hóa đại cương
Support: 0.01063394683026585
Confidence: 0.3291139240506329
Lift: 8.74656026417171
Rule: hóa đại cương -> bài tập toán học cao cấp
Support: 0.01063394683026585
Confidence: 0.2826086956521739
Lift: 8.74656026417171
Rule: bài tập toán học cao cấp -> 
Support: 0.011860940695296524
Confidence: 0.36708860759493667
Lift: 5.43958573072497
Rule:  -> bài tập toán học cao cấp
Support: 0.011860940695296524
Confidence: 0.17575757575757575
Lift: 5.43958573072497
Rule: bài tập toán học cao cấp -> bài tập vật lý 1 - phần cơ nhiệt
Support: 0.010224948875255624
Confidence: 0.3164556962025316
Lift: 5.526672694394213
Rule: bài tập vật lý 1 - phần cơ nhiệt -> bài tập toán học cao cấp
Support: 0.010224948875255624
Confidence: 0.17857142857142858
Lift: 5.526672694394213
Rule: bài tập toán học cao cấp -> bài tập toán học cao cấp
Support: 0.015541922290388548
Confidence: 0.48101265822784806
Lift: 16.564449991085752
Rule: bài tập toán học cao cấp -> bài tập toán 

#### Lưu kết quả

In [ ]:
df_rules = pd.DataFrame(data)

excel_filename = "Association_Rules.xlsx"
df_rules.to_excel(excel_filename, index=False)

print(f"Successfully saved association rules to {excel_filename}")